In [1]:
import pandas as pd 
import numpy as np

In [10]:
# Read the text file line by line
with open('C:/Users/ssarv/OneDrive/Desktop/Chrome Extension/ML/data/paragraphs.txt/paragraphs.txt', 'r') as file:
    paragraphs = file.readlines()


In [11]:
paragraphs[:5]

['This biographical article related to French artistic gymnastics is a stub. You can help Wikipedia by expanding it.\n',
 "InsideAR was the largest Augmented Reality event in Europe. It was organized and supported by metaio GmbH every year. The first event was held in 2010, had since expanded globally and was run at multiple locations around the world.  However, after Apple purchased metaio in May 2015, metaio cancelled the InsideAR conference 2015 without any statements about the conference's future. \n",
 'The Fearing Mind is an American horror television series that aired on the Fox Family Channel from October 21 until December 2, 2000. \n',
 'Bill Fearing, a famous writer of suspense thrillers, gets his ideas from things that happen in his family. When he gets an idea, the viewers enter his mind and see the gruesome events unfold. \n',
 'It had a bronze barrel and lacked a modern recoil system, using only an ineffective spring-mounted spade brake, and was virtually obsolescent on i

In [12]:
%pip install spacy
import spacy 


Note: you may need to restart the kernel to use updated packages.


In [17]:
#%%python -m spacy download en_core_web_sm
nlp = spacy.load("en_core_web_sm")
labeled_sentences = []
for para in paragraphs:
    para = para.strip()
    doc = nlp(para)
    sentences = [sent.text for sent in doc.sents]
    for i,sentence in enumerate(sentences):
        label = 1 if i==0 else 0
        print(label,sentence)
        labeled_sentences.append((sentence,label))


1 This biographical article related to French artistic gymnastics is a stub.
0 You can help Wikipedia by expanding it.
1 InsideAR was the largest Augmented Reality event in Europe.
0 It was organized and supported by metaio GmbH every year.
0 The first event was held in 2010, had since expanded globally and was run at multiple locations around the world.  
0 However, after Apple purchased metaio in May 2015, metaio cancelled the InsideAR conference 2015 without any statements about the conference's future.
1 The Fearing Mind is an American horror television series that aired on the Fox Family Channel from October 21 until December 2, 2000.
1 Bill Fearing, a famous writer of suspense thrillers, gets his ideas from things that happen in his family.
0 When he gets an idea, the viewers enter his mind and see the gruesome events unfold.
1 It had a bronze barrel and lacked a modern recoil system, using only an ineffective spring-mounted spade brake, and was virtually obsolescent on its intro

In [26]:
df = pd.DataFrame(labeled_sentences,columns=['sentence','label'])

In [28]:
df.head()

sentence  label
0  This biographical article related to French ar...      1
1            You can help Wikipedia by expanding it.      0
2  InsideAR was the largest Augmented Reality eve...      1
3  It was organized and supported by metaio GmbH ...      0
4  The first event was held in 2010, had since ex...      0

In [29]:
df.to_csv('labeled_sentence.csv',index=False)

In [2]:
labeled_df = pd.read_csv('labeled_sentence.csv')

In [3]:
labeled_df['label'].value_counts()

label
0    38709
1    31613
Name: count, dtype: int64

In [4]:
new_df = labeled_df.head(9999).copy()

In [5]:
new_df.count()

sentence    9999
label       9999
dtype: int64

In [42]:
%pip install transformers
%pip install torch


     ---------------------------------------- 0.0/43.6 kB ? eta -:--:--
     ----------------- -------------------- 20.5/43.6 kB 640.0 kB/s eta 0:00:01
     ----------------------------------- -- 41.0/43.6 kB 653.6 kB/s eta 0:00:01
     ----------------------------------- -- 41.0/43.6 kB 653.6 kB/s eta 0:00:01
     -------------------------------------- 43.6/43.6 kB 236.8 kB/s eta 0:00:00
   ---------------------------------------- 0.0/9.3 MB ? eta -:--:--
   - -------------------------------------- 0.4/9.3 MB 10.9 MB/s eta 0:00:01
   ----- ---------------------------------- 1.3/9.3 MB 13.9 MB/s eta 0:00:01
   -------- ------------------------------- 1.9/9.3 MB 13.7 MB/s eta 0:00:01
   --------- ------------------------------ 2.2/9.3 MB 11.5 MB/s eta 0:00:01
   ---------- ----------------------------- 2.5/9.3 MB 10.6 MB/s eta 0:00:01
   ----------- ---------------------------- 2.8/9.3 MB 10.4 MB/s eta 0:00:01
   ------------ --------------------------- 2.9/9.3 MB 9.3 MB/s eta 0:00:01
 

In [3]:
import torch

# Check if a GPU is available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

cpu


In [20]:
from transformers import BertTokenizer, BertModel
import numpy as np

# Load pre-trained BERT model and tokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertModel.from_pretrained('bert-base-uncased').to(device)

# Function to get sentence embeddings
def get_batch_embeddings(sentences):
    # Tokenize and process in batches
    inputs = tokenizer(sentences, return_tensors='pt', truncation=True, padding=True, max_length=512)
    inputs = {key: val.to(device) for key, val in inputs.items()}
    with torch.no_grad():
        outputs = model(**inputs)
    print('output sentences')
    return outputs.last_hidden_state.mean(dim=1).cpu().numpy()

# Split the DataFrame into batches
batch_size = 32  # Adjust batch size based on your hardware
batches = [new_df['sentence'][i:i + batch_size] for i in range(0, len(new_df), batch_size)]

# Initialize an empty list to hold all embeddings
all_embeddings = []

# Process each batch
for batch in batches:
    embeddings = get_batch_embeddings(batch.to_list())
    all_embeddings.extend(embeddings)

# Add embeddings to DataFrame
new_df['embedding'] = all_embeddings

# Save the DataFrame with embeddings to a CSV file
new_df.to_csv('labeled_sentences_with_embeddings.csv', index=False)





output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentences
output sentenc

In [11]:
# Apply the function to each sentence in the DataFrame
labeled_df['embedding'] = labeled_df['sentence'].apply(get_sentence_embedding)

In [ ]:
labeled_df.head()

In [6]:
new_df = pd.read_csv('labeled_sentences_with_embeddings.csv')

In [7]:
new_df.head()

sentence  label  \
0  This biographical article related to French ar...      1   
1            You can help Wikipedia by expanding it.      0   
2  InsideAR was the largest Augmented Reality eve...      1   
3  It was organized and supported by metaio GmbH ...      0   
4  The first event was held in 2010, had since ex...      0   

                                           embedding  
0  [-2.23362193e-01  1.25351995e-01  4.14817743e-...  
1  [ 4.21861887e-01 -4.09551173e-01  1.57263443e-...  
2  [-3.36665481e-01 -3.77468258e-01  7.39947617e-...  
3  [-2.77844608e-01 -2.26456463e-01  4.95387018e-...  
4  [-3.39705050e-01 -4.22247827e-01  4.49093878e-...

In [8]:
new_df.head(9999)

sentence  label  \
0     This biographical article related to French ar...      1   
1               You can help Wikipedia by expanding it.      0   
2     InsideAR was the largest Augmented Reality eve...      1   
3     It was organized and supported by metaio GmbH ...      0   
4     The first event was held in 2010, had since ex...      0   
...                                                 ...    ...   
9994  Like many others in its genus, it has a vining...      0   
9995  He married Maria D. White, of Danbury, in Octo...      1   
9996  Four of their children survived him and all of...      0   
9997        Averill's wife Maria died in February 1860.      1   
9998  In September 1861, he married Mary A. Perry, o...      0   

                                              embedding  
0     [-2.23362193e-01  1.25351995e-01  4.14817743e-...  
1     [ 4.21861887e-01 -4.09551173e-01  1.57263443e-...  
2     [-3.36665481e-01 -3.77468258e-01  7.39947617e-...  
3     [-2.77844608e-01 -2.26456463e-01  4.95387018e-...  
4     [-3.39705050e-01 -4.22247827e-01  4.49093878e-...  
...                                                 ...  
9994  [ 1.41215213e-02  2.26214621e-02  5.85948005e-...  
9995  [-1.14405252e-01 -3.26236128e-03 -8.06587711e-...  
9996  [-1.77615434e-01  1.13928720e-01  5.90706281e-...  
9997  [-3.62849645e-02  1.10571459e-01  1.39648840e-...  
9998  [-6.08606562e-02  8.81821141e-02 -2.15078387e-...  

[9999 rows x 3 columns]

In [9]:
new_df = pd.read_csv('labeled_sentences_with_embeddings.csv')

In [10]:
new_df['label'].value_counts()

label
0    5413
1    4586
Name: count, dtype: int64

In [11]:
new_df.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9999 entries, 0 to 9998
Data columns (total 3 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   sentence   9999 non-null   object
 1   label      9999 non-null   int64 
 2   embedding  9999 non-null   object
dtypes: int64(1), object(2)
memory usage: 234.5+ KB


In [ ]:
new_df['embedding'][0]

In [ ]:
new_df['embedding'].astype(float)

In [ ]:
new_df['embedding1'] = pd.to_numeric(new_df['embedding'])

In [15]:

from sklearn.model_selection import train_test_split

# Convert embeddings and labels to numpy arrays
X = np.array(new_df['embedding'].tolist())
y = new_df['label'].values

# Split the data into training and validation sets
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)


In [ ]:
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report

# Initialize and train the model
model = LogisticRegression(max_iter=1000)
model.fit(X_train, y_train)

# Make predictions
y_pred = model.predict(X_val)

# Evaluate the model
print(classification_report(y_val, y_pred))


In [ ]:
%pip install tensorflow transformers


In [ ]:
import tensorflow as tf
from transformers import BertTokenizer, TFBertModel
import pandas as pd

# Load pre-trained BERT model and tokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = TFBertModel.from_pretrained('bert-base-uncased')

# Function to get sentence embeddings
def get_batch_embeddings(sentences):
    # Tokenize and process in batches
    inputs = tokenizer(sentences, return_tensors='tf', truncation=True, padding=True, max_length=512)
    outputs = model(inputs)
    return tf.reduce_mean(outputs.last_hidden_state, axis=1).numpy()

# Load your DataFrame (assuming it's already loaded as `new_df`)
# new_df = pd.read_csv('your_file.csv')

# Split the DataFrame into batches
batch_size = 32  # Adjust batch size based on your hardware
batches = [new_df['sentence'][i:i + batch_size] for i in range(0, len(new_df), batch_size)]

# Initialize an empty list to hold all embeddings
all_embeddings = []

# Process each batch
for batch in batches:
    embeddings = get_batch_embeddings(batch.tolist())
    all_embeddings.extend(embeddings)

# Add embeddings to DataFrame
new_df['embedding'] = all_embeddings

# Save the DataFrame with embeddings to a CSV file
new_df.to_csv('labeled_sentences_with_embeddings.csv', index=False)
